In [1]:
import pandas as pd
import numpy as np

from scipy import stats
from statsmodels.stats import proportion
from statsmodels.stats.meta_analysis import effectsize_smd
from statsmodels.stats.power import tt_ind_solve_power, zt_ind_solve_power

from math import asin
import plotly.graph_objects as go
import plotly.express as px
from tqdm import tqdm_notebook
from typing import Union

In [2]:
data = pd.read_csv('gb_sem_9_cw.csv')

In [3]:
data

id     time  con_treat      page  converted
0       851104  11:48.6    control  old_page          0
1       804228  01:45.2    control  old_page          0
2       661590  55:06.2  treatment  new_page          0
3       853541  28:03.1  treatment  new_page          0
4       864975  52:26.2    control  old_page          1
...        ...      ...        ...       ...        ...
294473  751197  28:38.6    control  old_page          0
294474  945152  51:57.1    control  old_page          0
294475  734608  45:03.4    control  old_page          0
294476  697314  20:29.0    control  old_page          0
294477  715931  40:24.5  treatment  new_page          0

[294478 rows x 5 columns]

In [4]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 294478 entries, 0 to 294477
Data columns (total 5 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   id         294478 non-null  int64 
 1   time       294478 non-null  object
 2   con_treat  294478 non-null  object
 3   page       294478 non-null  object
 4   converted  294478 non-null  int64 
dtypes: int64(2), object(3)
memory usage: 11.2+ MB


In [5]:
from operator import mul

def convert_time(my_time: str):
    factors = (1, 1/60)
    time = sum(map(mul, map(float, my_time.split(':')), factors))
    return round(time, 2)

data.time = data.time.apply(convert_time)
data.con_treat.replace({'control': 0, 'treatment': 1}, inplace=True)
data.page.replace({'old_page': 0, 'new_page': 1}, inplace=True)

In [6]:
data

id   time  con_treat  page  converted
0       851104  11.81          0     0          0
1       804228   1.75          0     0          0
2       661590  55.10          1     1          0
3       853541  28.05          1     1          0
4       864975  52.44          0     0          1
...        ...    ...        ...   ...        ...
294473  751197  28.64          0     0          0
294474  945152  51.95          0     0          0
294475  734608  45.06          0     0          0
294476  697314  20.48          0     0          0
294477  715931  40.41          1     1          0

[294478 rows x 5 columns]

In [7]:
data.describe()

id           time      con_treat           page  \
count  294478.000000  294478.000000  294478.000000  294478.000000   
mean   787974.124733      30.052237       0.500126       0.500000   
std     91210.823776      17.303351       0.500001       0.500001   
min    630000.000000       0.000000       0.000000       0.000000   
25%    709032.250000      15.080000       0.000000       0.000000   
50%    787933.500000      30.060000       1.000000       0.500000   
75%    866911.750000      45.030000       1.000000       1.000000   
max    945999.000000      60.000000       1.000000       1.000000   

           converted  
count  294478.000000  
mean        0.119659  
std         0.324563  
min         0.000000  
25%         0.000000  
50%         0.000000  
75%         0.000000  
max         1.000000

In [8]:
data.con_treat.equals(data.page)

False

In [9]:
data.con_treat.compare(data.page).index

Int64Index([    22,    240,    308,    327,    357,    490,    685,    713,
               776,    846,
            ...
            293817, 293888, 293894, 293917, 293996, 294014, 294200, 294252,
            294253, 294331],
           dtype='int64', length=3893)

In [10]:
data.iloc[data.con_treat.compare(data.page).index, :]

id   time  con_treat  page  converted
22      767017  58.25          0     1          0
240     733976  11.27          0     1          0
308     857184  35.00          1     0          0
327     686623  26.68          1     0          0
357     856078  29.51          1     0          0
...        ...    ...        ...   ...        ...
294014  813406  25.55          1     0          0
294200  928506  32.17          0     1          0
294252  892498  11.18          1     0          0
294253  886135  49.34          0     1          0
294331  689637  34.47          0     1          0

[3893 rows x 5 columns]

In [11]:
data_2 = data.drop(data.con_treat.compare(data.page).index).copy(deep=True)

In [12]:
data_2

id   time  con_treat  page  converted
0       851104  11.81          0     0          0
1       804228   1.75          0     0          0
2       661590  55.10          1     1          0
3       853541  28.05          1     1          0
4       864975  52.44          0     0          1
...        ...    ...        ...   ...        ...
294473  751197  28.64          0     0          0
294474  945152  51.95          0     0          0
294475  734608  45.06          0     0          0
294476  697314  20.48          0     0          0
294477  715931  40.41          1     1          0

[290585 rows x 5 columns]

In [13]:
data_2.con_treat.equals(data_2.page)

True

In [14]:
data_2.id.value_counts()

773192    2
851104    1
688307    1
718297    1
838144    1
         ..
755610    1
804629    1
837875    1
889019    1
715931    1
Name: id, Length: 290584, dtype: int64

In [15]:
data_2 = data_2.loc[data_2.id.isin(data_2.id.value_counts()[data_2.id.value_counts() == 1].index.values), :]

In [16]:
def is_normal_distr(x):
    
    if x.size < 5_000:
        _, pvalue = stats.shapiro(x)
    else:
        _, pvalue = stats.kstest(x, 'norm')
        
    return pvalue

In [17]:
def calc_continuous_effect(control: pd.DataFrame,
                           treatment: pd.DataFrame,
                           column: str,
                           stat_test: Union['t', 'mw'] = 't') -> pd.DataFrame:
    
    control_mean = control.loc[:, column].mean()
    treatment_mean = treatment.loc[:, column].mean()
    
    control_std = control.loc[:, column].std(ddof=1)
    treatment_std = treatment.loc[:, column].std(ddof=1)
    
    nobs1 = control.shape[0]
    nobs2 = treatment.shape[0]
    
    # effect_size = (treatment_mean - control_mean) / ((control_std ** 2 + treatment_std ** 2) / 2) ** .5
    effect_size, _ = effectsize_smd(mean1=treatment_mean, sd1=treatment_std, nobs1=nobs2,
                                    mean2=control_mean, sd2=control_std, nobs2=nobs1)
    
    if stat_test == 't':
        _, pvalue = stats.ttest_ind(a=control.loc[:, column],
                                    b=treatment.loc[:, column],
                                    equal_var=False, # perform Welch's t-test
                                    alternative='two-sided')
   
    elif stat_test == 'mw':
        _, pvalue = stats.mannwhitneyu(x=control.loc[:, column],
                                       y=treatment.loc[:, column],
                                       alternative='two-sided')
    else:
        raise NotImplementedError()

    power = tt_ind_solve_power(effect_size=effect_size,
                               nobs1=control.shape[0],
                               alpha=0.05,
                               power=None,
                               ratio=nobs2/nobs1)
    
    pw_settings = {'alpha': .05, 'power': .8}
    pw_nobs = tt_ind_solve_power(effect_size=effect_size,
                                 nobs1=None,
                                 alpha=pw_settings['alpha'],
                                 power=pw_settings['power'],
                                 ratio=1)
    
    difference = treatment_mean - control_mean
    
    result = pd.DataFrame({'effect_size': effect_size,
                           'alpha': pvalue, 
                           'beta': (1-power),
                           'power': power,
                           'difference': difference,
                           'nobs': nobs1 + nobs2},
                          index=[column]) 
    
    perfect_way = pd.DataFrame({'effect_size': effect_size,
                                'alpha': pw_settings['alpha'],
                                'beta': 1 - pw_settings['power'],
                                'power': pw_settings['power'],
                                'difference': difference,
                                'nobs': round(pw_nobs * 2, 0)},
                               index=['perfect_way'])
    
    return pd.concat((result, perfect_way))

In [18]:
def calc_proportion_effect(control: pd.DataFrame,
                           treatment: pd.DataFrame,
                           column: str,) -> pd.DataFrame:
    
    control_mean = control.loc[:, column].mean()
    treatment_mean = treatment.loc[:, column].mean()
    
    conv1 = control.loc[:, column].sum()
    conv2 = treatment.loc[:, column].sum()
    
    nobs1 = control.shape[0]
    nobs2 = treatment.shape[0]
    
    # effect_size_f = 2  * asin(np.sqrt(conv1/nobs1)) - 2 * asin(np.sqrt(conv2/nobs2))
    effect_size = proportion.proportion_effectsize(prop1=conv1/nobs1, prop2=conv2/nobs2)
    
    _, chi_pvalue, _ = proportion.proportions_chisquare([conv1, conv2], [nobs1, nobs2])
    
    _, z_pvalue = proportion.proportions_ztest([conv1, conv2], [nobs1, nobs2])

    power = zt_ind_solve_power(effect_size=effect_size,
                               nobs1=nobs1,
                               alpha=0.05,
                               power=None,
                               ratio=nobs2/nobs1)
    
    pw_settings = {'alpha': .05, 'power': .8}
    pw_nobs = zt_ind_solve_power(effect_size=effect_size,
                                 nobs1=None,
                                 alpha=pw_settings['alpha'],
                                 power=pw_settings['power'],
                                 ratio=1)
    
    difference = treatment_mean - control_mean
    
    result = pd.DataFrame({'effect_size': effect_size,
                           'alpha_chi': chi_pvalue, 
                           'alpha_z': z_pvalue,
                           'beta': (1-power),
                           'power': power,
                           'difference': difference,
                           'nobs': nobs1 + nobs2},
                          index=[column]) 
    
    perfect_way = pd.DataFrame({'effect_size': effect_size,
                                'alpha_chi': pw_settings['alpha'],
                                'alpha_z': pw_settings['alpha'],
                                'beta': 1 - pw_settings['power'],
                                'power': pw_settings['power'],
                                'difference': difference,
                                'nobs': round(pw_nobs * 2, 0)},
                               index=['perfect_way'])
    
    return pd.concat((result, perfect_way))

In [19]:
control = data_2[data_2.con_treat == 0].copy()
treatment = data_2[data_2.con_treat == 1].copy()

In [20]:
### Testing timespent
control.shape, treatment.shape

((145274, 5), (145309, 5))

In [21]:
fig = go.Figure()
fig.add_trace(go.Histogram(x=control.time, name='control',))
fig.add_trace(go.Histogram(x=treatment.time, name='treatment',))

# Overlay both histograms
fig.update_layout(barmode='overlay')
# Reduce opacity to see both histograms
fig.update_traces(opacity=0.5)
fig.show()

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

In [ ]:
is_normal_distr(control.time), is_normal_distr(treatment.time)

(0.0, 0.0)

In [ ]:
#!pip install distfit -U

In [ ]:
from distfit import distfit

# Initialize for discrete distribution fitting
dfit = distfit()

# Run distfit to and determine whether we can find the parameters from the data.
result = dfit.fit_transform(treatment.time)

[distfit] >INFO> fit
[distfit] >INFO> transform
[distfit] >INFO> [norm      ] [0.00 sec] [RSS: 0.00191014] [loc=30.025 scale=17.318]
[distfit] >INFO> [expon     ] [0.00 sec] [RSS: 0.00373173] [loc=0.000 scale=30.025]
[distfit] >INFO> [pareto    ] [0.16 sec] [RSS: 0.00373173] [loc=-2147483648.000 scale=2147483648.000]
[distfit] >INFO> [dweibull  ] [1.53 sec] [RSS: 0.00195711] [loc=30.435 scale=16.542]
[distfit] >INFO> [t         ] [10.3 sec] [RSS: 0.00190982] [loc=30.025 scale=17.319]
[distfit] >INFO> [genextreme] [2.97 sec] [RSS: 0.00171486] [loc=25.284 scale=18.256]
[distfit] >INFO> [gamma     ] [0.70 sec] [RSS: 0.00191026] [loc=-7482.208 scale=0.040]
[distfit] >INFO> [lognorm   ] [5.75 sec] [RSS: 0.00192861] [loc=-655.249 scale=685.084]
[distfit] >INFO> [beta      ] [4.37 sec] [RSS: 1.968e-05] [loc=-0.015 scale=60.015]
[distfit] >INFO> [uniform   ] [0.00 sec] [RSS: 5.34571e-06] [loc=0.000 scale=60.000]
[distfit] >INFO> [loggamma  ] [1.93 sec] [RSS: 0.00190071] [loc=-2553.568 scale=40

In [ ]:
result['model']

{'name': 'uniform',
 'score': 5.345708920544096e-06,
 'loc': 0.0,
 'scale': 60.0,
 'arg': (),
 'params': (0.0, 60.0),
 'model': <scipy.stats._distn_infrastructure.rv_continuous_frozen at 0x1e9777b1490>,
 'bootstrap_score': 0,
 'bootstrap_pass': None,
 'color': '#e41a1c',
 'CII_min_alpha': 3.0,
 'CII_max_alpha': 57.0}

In [ ]:
calc_continuous_effect(control, treatment, 'time', 'mw')

effect_size     alpha      beta     power  difference       nobs
time           -0.003291  0.377299  0.856127  0.143873   -0.056942   290583.0
perfect_way    -0.003291  0.050000  0.200000  0.800000   -0.056942  2898196.0

In [ ]:
### Bootstrap
n = 10000
sample_size = max(control.shape[0], treatment.shape[0])
sample_mean = []
for _ in tqdm_notebook(range(n)):
    sample_control = control.time.sample(n=sample_size, replace=True, random_state=_)
    sample_treatment = treatment.time.sample(n=sample_size, replace=True, random_state=_)
    sample_mean.append(np.mean(sample_treatment.values - sample_control.values))

  0%|          | 0/10000 [00:00<?, ?it/s]

In [ ]:
fig = px.histogram(pd.DataFrame({'mean': sample_mean}),
                   x='mean',
                   title='sample of mean diff',
                   marginal = 'box',
                   nbins = 50)
fig.show()

In [ ]:
is_normal_distr(np.array(sample_mean))

0.0

In [ ]:
np.quantile(sample_mean, [.025, 0.5, 0.975])

array([-0.1828877 , -0.05675915,  0.06697561])

In [ ]:
norm_generator = stats.norm(loc=np.mean(sample_mean), scale=np.std(sample_mean, ddof=1))
p_value = min(norm_generator.cdf(0), norm_generator.sf(0)) * 2
p_value

0.3725603124269764

In [ ]:
### Bucket

In [ ]:
data_2.shape[0] 

290583

In [ ]:
for _ in range(100, 1001): 
    if data_2.shape[0] % _ == 0:
        print(_)

249
389
747


In [ ]:
n_buckets = 747
data_2 = data_2.assign(bucket=list(range(n_buckets)) * int(data_2.shape[0] / n_buckets))

In [ ]:
data_2.head()

id   time  con_treat  page  converted  bucket
0  851104  11.81          0     0          0       0
1  804228   1.75          0     0          0       1
2  661590  55.10          1     1          0       2
3  853541  28.05          1     1          0       3
4  864975  52.44          0     0          1       4

In [ ]:
backeted_data_2 = data_2.groupby(['con_treat', 'bucket'])['time'].agg(mu=np.mean, std=np.std).reset_index()
backeted_data_2

con_treat  bucket         mu        std
0             0       0  29.866698  17.604727
1             0       1  29.750652  17.592327
2             0       2  30.777563  18.129486
3             0       3  30.419901  17.289409
4             0       4  30.928750  18.137678
...         ...     ...        ...        ...
1489          1     742  32.494787  17.600433
1490          1     743  29.702903  18.462280
1491          1     744  31.363854  16.620880
1492          1     745  30.884737  18.121323
1493          1     746  30.197286  17.548639

[1494 rows x 4 columns]

In [ ]:
# Сравним исходное выборочное среднее и среднее бакетных средних 
round(np.mean(data_2["time"]), 5), round(np.mean(backeted_data_2["mu"]), 5)

(30.05361, 30.05585)

In [ ]:
round(np.std(data_2["time"]), 5), round(np.mean(backeted_data_2["std"]), 5)

(17.30051, 17.29103)

In [ ]:
control_b = backeted_data_2[backeted_data_2.con_treat == 0].copy()
treatment_b = backeted_data_2[backeted_data_2.con_treat == 1].copy()

n = 10000
sample_size = max(control_b.shape[0], treatment_b.shape[0])
sample_mean = []

for _ in tqdm_notebook(range(n)):
    sample_control = control_b.mu.sample(n=sample_size, replace=True, random_state=_)
    sample_treatment = treatment_b.mu.sample(n=sample_size, replace=True, random_state=_)
    sample_mean.append(np.mean(sample_treatment.values - sample_control.values))

  0%|          | 0/10000 [00:00<?, ?it/s]

In [ ]:
fig = px.histogram(pd.DataFrame({'mean':sample_mean}),
                   x='mean',
                   title='sample of mean diff',
                   marginal = 'box',
                   nbins = 100)
fig.show()

In [ ]:
np.quantile(sample_mean, [.025, 0.5, 0.975]) #array([-0.17896708, -0.05758005,  0.06815545])

array([-0.18255822, -0.05918222,  0.06602771])

In [ ]:
norm_generator = stats.norm(loc=np.mean(sample_mean), scale=np.std(sample_mean, ddof=1))
p_value = min(norm_generator.cdf(0), norm_generator.sf(0)) * 2
p_value

0.3580374286856399

In [ ]:
### Testing converted

In [ ]:
fig = go.Figure()
fig.add_trace(go.Histogram(x=control.converted, name='control',))
fig.add_trace(go.Histogram(x=treatment.converted, name='treatment',))

# Overlay both histograms
fig.update_layout()
# Reduce opacity to see both histograms
fig.update_traces(opacity=0.5)
fig.show()

In [ ]:
calc_proportion_effect(control, treatment, 'converted')

effect_size  alpha_chi   alpha_z      beta     power  difference  \
converted       0.004861   0.190114  0.190114  0.741525  0.258475   -0.001577   
perfect_way     0.004861   0.050000  0.050000  0.200000  0.800000   -0.001577   

                  nobs  
converted     290583.0  
perfect_way  1328527.0

In [ ]:
df = pd.read_csv('data/gb_sem_9_hw.csv')

In [ ]:
df

userid  version  sum_gamerounds  retention_1  retention_7
0          116  gate_30               3        False        False
1          337  gate_30              38         True        False
2          377  gate_40             165         True        False
3          483  gate_40               1        False        False
4          488  gate_40             179         True         True
...        ...      ...             ...          ...          ...
90184  9999441  gate_40              97         True        False
90185  9999479  gate_40              30        False        False
90186  9999710  gate_30              28         True        False
90187  9999768  gate_40              51         True        False
90188  9999861  gate_40              16        False        False

[90189 rows x 5 columns]

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 90189 entries, 0 to 90188
Data columns (total 5 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   userid          90189 non-null  int64 
 1   version         90189 non-null  object
 2   sum_gamerounds  90189 non-null  int64 
 3   retention_1     90189 non-null  bool  
 4   retention_7     90189 non-null  bool  
dtypes: bool(2), int64(2), object(1)
memory usage: 2.2+ MB


In [ ]:
df.userid.nunique()

90189